- Sharpe ratio

- Sortino ratio

- Modigliani ratio

- Calmar ratio

- Max Drawdown

In [1]:
import datetime as dt 
import numpy as np
import pandas as pd
import plotly.offline as pyo
from pandas_datareader import data as pdr

import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [2]:
pyo.init_notebook_mode(connected=True)
pd.options.plotting.backend = "plotly"

In [3]:
end = dt.datetime.now()
start = dt.datetime(2015,1,1)

df = pdr.get_data_yahoo(['^AXJO','CBA.AX','NAB.AX','STO.AX','WPL.AX'], start, end)

Close = df.Close
Close.head()

Symbols           ^AXJO     CBA.AX     NAB.AX    STO.AX     WPL.AX
Date                                                              
2015-01-01  5435.899902  85.277962  31.925041  7.132698  37.629452
2015-01-04  5450.299805  85.486832  31.972605  7.193661  37.826828
2015-01-05  5364.799805  84.840332  31.715757  6.575320  35.981377
2015-01-06  5353.600098  84.651360  31.791861  6.488230  35.665577
2015-01-07  5381.500000  84.929848  32.077248  6.357594  35.487938

In [4]:
# log returns

log_returns = np.log(df.Close/df.Close.shift(1)).dropna()
log_returns

Symbols        ^AXJO    CBA.AX    NAB.AX    STO.AX    WPL.AX
Date                                                        
2015-01-04  0.002646  0.002446  0.001489  0.008511  0.005232
2015-01-05 -0.015812 -0.007591 -0.008066 -0.089877 -0.050017
2015-01-06 -0.002090 -0.002230  0.002397 -0.013333 -0.008815
2015-01-07  0.005198  0.003284  0.008937 -0.020340 -0.004993
2015-01-08  0.015507  0.007583  0.015011  0.052046  0.029861
...              ...       ...       ...       ...       ...
2021-05-19 -0.019189 -0.025276 -0.013362 -0.022504 -0.025998
2021-05-20  0.012601  0.031801  0.016013 -0.012885 -0.001787
2021-05-21  0.001523 -0.003563  0.001134 -0.048718 -0.034117
2021-05-24  0.002217  0.007215  0.006777  0.019476  0.012417
2021-05-25  0.009787  0.008771  0.008593  0.001483  0.006378

[1615 rows x 5 columns]

# Calculate daily standard deviation of returns

In [5]:
daily_std = log_returns.std()
daily_std

Symbols
^AXJO     0.010532
CBA.AX    0.014510
NAB.AX    0.015688
STO.AX    0.029588
WPL.AX    0.019065
dtype: float64

In [6]:
annualized_std = daily_std*np.sqrt(252)
annualized_std*100

Symbols
^AXJO     16.719255
CBA.AX    23.033989
NAB.AX    24.904165
STO.AX    46.968789
WPL.AX    30.264056
dtype: float64

# Plot histogram of log returns with annualized volatility

In [7]:
fig = make_subplots(rows=2,cols=2)
trace0 = go.Histogram(x=log_returns['CBA.AX'], name='CBA')
trace1 = go.Histogram(x=log_returns['NAB.AX'], name='NAB')
trace2 = go.Histogram(x=log_returns['STO.AX'], name='STO')
trace3 = go.Histogram(x=log_returns['WPL.AX'], name='WPL')

fig.append_trace(trace0, 1, 1)
fig.append_trace(trace1, 1, 2)
fig.append_trace(trace2, 2, 1)
fig.append_trace(trace3, 2, 2)

fig.update_layout(autosize = False, width=700, height=600, title='Frequency of log returns',
                  xaxis=dict(title='CBA Annualized Volatility: ' + str(np.round(annualized_std['CBA.AX']*100, 1))),
                  xaxis2=dict(title='NAB Annualized Volatility: ' + str(np.round(annualized_std['NAB.AX']*100, 1))),
                  xaxis3=dict(title='STO Annualized Volatility: ' + str(np.round(annualized_std['STO.AX']*100, 1))),
                  xaxis4=dict(title='WPL Annualized Volatility: ' + str(np.round(annualized_std['WPL.AX']*100, 1))))

fig.show()


In [8]:
trading_days = 60
volatility = log_returns.rolling(window=trading_days).std()*np.sqrt(trading_days)

In [9]:
volatility.plot()

# Sharpe Ratio

The Sharpe ratio which was introduced in 1966 by Nobel laureate William F. Sharpe is a measure for calculating risk-adjusted return. The Sharpe ratio is the average return earned in excess of the risk-free rate per unit of volatility.

In [10]:
Rf = 0.01/252 # risk free rate (daily)
sharpe_ratio = (log_returns.rolling(window=trading_days).mean() - Rf)*trading_days/volatility
sharpe_ratio.plot()

# Sortino Ratio

The Sortino ratio is very similar to the Sharpe ratio, the only difference being that where the Sharpe ratio uses all the observations for calculating the standard deviation the Sortino ratio only considers the harmful variance.

In [11]:
sortino_vol = log_returns[log_returns < 0].rolling(window=trading_days, center=True, min_periods=10).std()*np.sqrt(trading_days)

sortino_ratio = (log_returns.rolling(window=trading_days).mean() - Rf)*trading_days / sortino_vol

sortino_vol.plot()


In [12]:
sortino_ratio.plot()

# Modigliani Ratio (M2 Ratio)

The Modigliani ratio measures the returns of the portfolio, adjusted for the risk of the portfolio relative to that of some benchmark.

In [13]:
m2_ratio = pd.DataFrame()

benchmark_volatility = volatility['^AXJO']
for c in log_returns.columns:
    if c != '^AXJO':
        m2_ratio[c] = (sharpe_ratio[c]*benchmark_volatility/trading_days + Rf)*trading_days

m2_ratio.plot().update_layout(autosize = False, width=600, height=300)

# Max Drawdown

Max drawdown quantifies the steepest decline from peak to trough observed for an investment. This is useful for a number of reasons, mainly the fact that it doesn't rely on the underlying returns being normally distributed.

In [14]:
def max_drawdown(returns):
    cumulative_returns = (returns+1).cumprod()
    peak = cumulative_returns.expanding(min_periods=1).max()
    drawdown = (cumulative_returns/peak) - 1
    return drawdown.min()

returns = df.Close.pct_change()
max_drawdowns = returns.apply(max_drawdown, axis=0)
max_drawdowns*100

Symbols
^AXJO    -36.530541
CBA.AX   -43.361732
NAB.AX   -63.126540
STO.AX   -69.444444
WPL.AX   -60.846153
dtype: float64

# Calmar Ratio

Calmar ratio uses max drawdown in the denominator as opposed to standard deviation. 

In [15]:
calmars = np.exp(log_returns.mean()*252)/abs(max_drawdowns)
calmars.plot.bar().update_layout(autosize=False, width=600, height=400)